# Vestwell Python Screener

If you have any questions or feel you are making assumptions, please record them in this notebook or in comments if you'd rather work in a `.py` file.  If you get stuck, try to explain in words how you would complete the exercise.

### Background

Vestwell provides a wide variety of investment choices to its users.  Participants in a retirement plan can choose between a pre-determined set of funds or they can choose their own custom set of funds from a list of choices.  Advisors can create their own models with a custom set of funds in which participants can choose to invest.  As a result, there are thousands of unique models on the Vestwell platform.  

One of Vestwell's partners has the same list of models in its database.  This partner will maintain an up-to-date list of funds for each model in their database.  For example, when a fund closes and is replaced by a new one, Vestwell's partner will update the model with the new fund in their database, but not in Vestwell's.  For this reason, Vestwell's database and our partner's database will get out of sync over time.  Unless, that is, you can build python script to reconcile the two databases.  We're rooting for you!

### The Data

Here's a high-level overview of the data.  We'll get into more details below as we dig in.

**Vestwell Data**

Each `program_id` has many `model_id`s.  Each `model_id` has many `symbol`s.

* model.csv:  Associations of programs to models.
* model_prop.csv:  Association of models to symbols.

**Partner Data**

Each `PLANID` has many `FUNDID`s.

* partner.csv:  Association of `PLANID` to `FUNDID` and `PLANINVCLOSEDATE`.  

**Some extra notes**

* The `FUNDID` in our partner's data is equivalent to `symbol` in Vestwell's data.  These are also referred to as "funds".
* The `PLANID` in our partner's data has information that is equivalent to the `program_id` in Vestwell's database (more details below in Step 2).
* The `PLANINVCLOSEDATE` in our partner's database is the date when a fund was closed.  If there isn't a date, then the fund has not been closed.
* Sometimes our partner has funds called either "Medicham" or "Electrike" which we ignore.

### Goal
The goal of this exercise is to compare Vestwell's data with our partner's data.  We want to figure out if Vestwell's model data is the same as our Partner's data.  We consider our partner's database the source of truth since their database will remain updated if there are any changes to funds.  Here's specifically what we are asking:

1.  Do the list of funds for each `model_id` in each `program_id` in Vestwell's database match the list of funds in our partner's `program_id`?  If there are any mismatches, what funds are missing from each database?  Remember, our partner doesn't use `model_id` so whichever funds they have for a particular `program_id` should match the list of funds that Vestwell has for any `model_id` that uses that `program_id`.

For example, if Vestwell's database has funds A, B and C for a `model_id` in a particular `program_id` and our partner's database has funds B, C, and D for the same `program_id` we would report that fund A is missing from our partner's database and that fund D is missing from our database for that `model_id` and `program_id`.

2.  Are there any funds in Vestwell's database that have closed?  If so, what are they for each `model_id` in each `program_id`?

For example, if our database has funds D, E, and F for a certain `model_id` in a `program_id` and our partner's database shows that fund D closed on 11/1/2019, then we would report that fund D has closed for that `model_id` and `program_id`.

Ideally, the output is in a form that can be passed to a Business Analyst to take action on.  For example, the output could look something like this:

| program_id | model_id | fund_missing_at_vw | fund_missing_at_partner | fund_closed |
|------------|--|---------------|--------------------|--------|
| 1          |1| None          | None               | None   |
| 1          |2| D, Z             | A                  | F   |
| 2          |2| None             | None               | F      |

### Some Hints
* We value correct output over efficient code.  
* Does your code execute fully without errors?
* What edge cases have you considered?  How could you handle them?
* Could another engineer read your code and easily understand what's going on and why you did things a certain way?
* Most analysts don't use Python or Jupyter Notebooks.  How could you give them the output of your code?

You should find the following mismatches for `program_id` 1 and `model_id` 268:
* Funds missing at Vestwell: 
    
        'Hitmontop',
        'Smoochum',
        'Gastly',
        'Teddiursa',
        'Meowth',
        'Sneasel',
        'Xatu',
        'Growlithe',
        'Torchic',
        'ManectricMega Manectric',
        'Smeargle',
        'Stantler',
        'Tyrogue'
    
    
* Funds missing at Partner:
    
        'Persian', 'Psyduck', 'Rattata', 'Dugtrio'
    
    
* Closed funds:

        None

## Table Schema


![Schema](data/Vestwell_challange.png)

# Step 0
Import any packages you'll need

In [124]:
import pandas as pd
import numpy as np
import math
import copy

In [50]:
pd.set_option('display.max_rows', 800)
pd.set_option('display.max_colwidth', None)

# Step 1
Import `partner.csv`, `model.csv`, and `model_prop.csv`.

In [2]:
model = pd.read_csv('data_V2/model.csv')
model.head()

model_id  program_id
0        28           3
1        34           4
2        42           4
3        24           3
4        64           8

In [3]:
model.shape

(187, 2)

In [4]:
model_prop = pd.read_csv('data_V2/model_props.csv')
model_prop.head()

model_props_id  model_id                 symbol
0             541        80              Bulbasaur
1             542        80                Ivysaur
2             543        80               Venusaur
3             544        80  VenusaurMega Venusaur
4             545        80             Charmander

In [5]:
model_prop.shape

(729, 3)

In [6]:
partner = pd.read_csv('data_V2/partner.csv')
partner.head()

PLANID PLANINVCLOSEDATE    FUNDID
0  VW0008000039           active  Medicham
1  VW0008000039           active  Arcanine
2  VW0008000039       11/01/2018  Clefairy
3  VW0008000039           active     Zubat
4  VW0008000039           active  Nidoking

In [7]:
partner.shape

(445, 3)

# Step 2 - working with the `partner.csv` data
Extract the `program_id` from the `PLANID` column in the `partner` dataframe.  The `program_id` is the first four characters in `PLANID` after "VW".  It's usually an integer.  If instead of digits, those characters are equal to "PALL" then the `program_id` = 1.  Drop any other rows remaining that do not have four digits in the first four characters after "VW" in the `PLANID` column.  For example, if a row in `PLANID` has `VWLASP000` then it should be dropped because it has `LASP` after `VW` instead of four digits.

In [9]:
#extracts plann number for partner.PLANID col, will return NA for any non 'PALL' of numeric value
def get_plan(plan_id):
    if plan_id[2:6]=='PALL':
        return 1
    #need to remove leading zeros 00
    #try except will only return the int on 2:6 if its a number
    try:   
        return int(plan_id[2:6])
    #otherwise return nan to be dropped
    except:
        return np.nan

In [10]:
partner.head(10)

PLANID PLANINVCLOSEDATE                     FUNDID
0  VW0008000039           active                   Medicham
1  VW0008000039           active                   Arcanine
2  VW0008000039       11/01/2018                   Clefairy
3  VW0008000039           active                      Zubat
4  VW0008000039           active                   Nidoking
5  VW0008000039           active                 Jigglypuff
6  VW0008000039           active  CharizardMega Charizard X
7  VW0008000039           active                  Electrike
8  VW0008000039           active                  Growlithe
9  VW0008000039           active                     Fearow

In [11]:
partner['partner_program_id'] = 0

In [12]:
partner.partner_program_id = partner.PLANID.apply(lambda x: get_plan(x))

In [14]:
#need to drop the NAN columns
partner.dropna(inplace=True)

In [15]:
partner.partner_program_id.value_counts()

27    39
9     36
15    35
8     31
12    28
30    26
21    25
14    25
13    25
20    24
17    24
29    22
19    20
16    19
1     18
28    17
24    16
10    15
Name: partner_program_id, dtype: int64

In [16]:
partner.shape

(445, 4)

In [17]:
partner.head(10)

PLANID PLANINVCLOSEDATE                     FUNDID  \
0  VW0008000039           active                   Medicham   
1  VW0008000039           active                   Arcanine   
2  VW0008000039       11/01/2018                   Clefairy   
3  VW0008000039           active                      Zubat   
4  VW0008000039           active                   Nidoking   
5  VW0008000039           active                 Jigglypuff   
6  VW0008000039           active  CharizardMega Charizard X   
7  VW0008000039           active                  Electrike   
8  VW0008000039           active                  Growlithe   
9  VW0008000039           active                     Fearow   

   partner_program_id  
0                   8  
1                   8  
2                   8  
3                   8  
4                   8  
5                   8  
6                   8  
7                   8  
8                   8  
9                   8

# Step 3
Check if the funds match for each `program_id`.  In `partner.csv` the funds are in the `FUNDID` column and for `model_prop.csv` the funds are in the `symbol` column.  If there are any mismatches, return a list of which funds are missing from each database for each `model_id` in each `program_id`.

### Merge model and model_prop df on model_id column

In [20]:
vw_df = pd.merge(model, model_prop,  how='left', left_on=['model_id'], 
                     right_on = ['model_id'])

In [21]:
vw_df.model_id.value_counts().count()

187

#### Note no model_ids were dropped using left join

In [22]:
model.model_id.value_counts().count()

187

In [23]:
model_prop.model_id.value_counts().count()

187

#### Looking at values (delete later)

In [ ]:
model[model.model_id==28]

In [ ]:
model_prop[model_prop.model_id==28]

In [ ]:
vw_df.head(10)

In [ ]:
vw_df.shape

In [ ]:
vw_df.isnull().sum()

### Now combine vw_df with partner

In [25]:
combined_df = pd.merge(partner, vw_df,  how='outer', left_on=['FUNDID', 'partner_program_id'], 
                     right_on = ['symbol','program_id'])

In [26]:
combined_df

PLANID PLANINVCLOSEDATE    FUNDID  partner_program_id  model_id  \
0    VW0008000039           active  Medicham                 8.0       NaN   
1    VW0008000039           active  Arcanine                 8.0      65.0   
2    VW0008000039       11/01/2018  Clefairy                 8.0      65.0   
3    VW0008000039           active     Zubat                 8.0      65.0   
4    VW0008000039           active  Nidoking                 8.0      65.0   
..            ...              ...       ...                 ...       ...   
780           NaN              NaN       NaN                 NaN     278.0   
781           NaN              NaN       NaN                 NaN     279.0   
782           NaN              NaN       NaN                 NaN     280.0   
783           NaN              NaN       NaN                 NaN     281.0   
784           NaN              NaN       NaN                 NaN     282.0   

     program_id  model_props_id      symbol  
0           NaN             NaN         NaN  
1           8.0           311.0    Arcanine  
2           8.0           297.0    Clefairy  
3           8.0           304.0       Zubat  
4           8.0           296.0    Nidoking  
..          ...             ...         ...  
780        26.0          1962.0     Metapod  
781        26.0          1963.0  Butterfree  
782        26.0          1964.0      Weedle  
783        26.0          1965.0      Kakuna  
784        26.0          1966.0    Beedrill  

[785 rows x 8 columns]

In [27]:
combined_df.shape

(785, 8)

In [28]:
combined_df.program_id.value_counts().sum()

729

In [29]:
combined_df.partner_program_id.value_counts().sum()

509

In [30]:
combined_df[(combined_df.partner_program_id==1)|(combined_df.program_id==1)]

PLANID PLANINVCLOSEDATE     FUNDID  partner_program_id  model_id  \
482  VWPALL000076           active   Medicham                 1.0       NaN   
483  VWPALL000076           active  Hitmontop                 1.0     269.0   
484  VWPALL000076           active   Smoochum                 1.0     269.0   
485  VWPALL000076           active    Diglett                 1.0     268.0   
486  VWPALL000076           active    Diglett                 1.0     269.0   
..            ...              ...        ...                 ...       ...   
668           NaN              NaN        NaN                 NaN     262.0   
669           NaN              NaN        NaN                 NaN     259.0   
670           NaN              NaN        NaN                 NaN     260.0   
671           NaN              NaN        NaN                 NaN     259.0   
672           NaN              NaN        NaN                 NaN     261.0   

     program_id  model_props_id     symbol  
482         NaN             NaN        NaN  
483         1.0          1906.0  Hitmontop  
484         1.0          1910.0   Smoochum  
485         1.0          1897.0    Diglett  
486         1.0          1907.0    Diglett  
..          ...             ...        ...  
668         1.0          1862.0    Venonat  
669         1.0          1838.0    Donphan  
670         1.0          1846.0    Donphan  
671         1.0          1839.0   Porygon2  
672         1.0          1854.0   Porygon2  

[84 rows x 8 columns]

### Drop Columns with "Medicham" or "Electrike"

In [31]:
dropindex = combined_df[combined_df['FUNDID'] == 'Medicham' ].index

In [32]:
#delete later
dropindex

Int64Index([0, 76, 91, 145, 223, 272, 305, 331, 347, 396, 443, 482], dtype='int64')

In [33]:
combined_df.drop(dropindex, inplace=True)

In [34]:
dropindex = combined_df[combined_df['FUNDID'] == 'Electrike' ].index

In [35]:
#delete later
dropindex

Int64Index([  7,  61,  88, 114, 131, 152, 185, 220, 229, 262, 295, 320, 342,
            372, 408, 430, 450, 500],
           dtype='int64')

In [36]:
combined_df.drop(dropindex, inplace=True)

In [37]:
combined_df.fillna('missing', inplace=True)

### Funds removed that are closed
ie MedichamMega Medicham & Manectric

In [39]:
partner[partner.partner_program_id==1]

PLANID PLANINVCLOSEDATE                   FUNDID  \
427  VWPALL000076           active                 Medicham   
428  VWPALL000076           active                Hitmontop   
429  VWPALL000076           active                 Smoochum   
430  VWPALL000076           active                  Diglett   
431  VWPALL000076       01/15/2019    MedichamMega Medicham   
432  VWPALL000076           active                   Gastly   
433  VWPALL000076           active                Teddiursa   
434  VWPALL000076           active                   Meowth   
435  VWPALL000076           active                  Sneasel   
436  VWPALL000076           active                Electrike   
437  VWPALL000076           active                     Xatu   
438  VWPALL000076           active                Growlithe   
439  VWPALL000076           active                  Torchic   
440  VWPALL000076       09/27/2017                Manectric   
441  VWPALL000076           active  ManectricMega Manectric   
442  VWPALL000076           active                 Smeargle   
443  VWPALL000076           active                 Stantler   
444  VWPALL000076           active                  Tyrogue   

     partner_program_id  
427                   1  
428                   1  
429                   1  
430                   1  
431                   1  
432                   1  
433                   1  
434                   1  
435                   1  
436                   1  
437                   1  
438                   1  
439                   1  
440                   1  
441                   1  
442                   1  
443                   1  
444                   1

In [40]:
vw_df[vw_df.model_id==268]

model_id  program_id  model_props_id   symbol
40       268           1            1899  Persian
41       268           1            1897  Diglett
42       268           1            1900  Psyduck
43       268           1            1896  Rattata
44       268           1            1898  Dugtrio

In [41]:
combined_df[combined_df.model_id==268]

PLANID PLANINVCLOSEDATE   FUNDID partner_program_id model_id  \
485  VWPALL000076           active  Diglett                  1      268   
562       missing          missing  missing            missing      268   
569       missing          missing  missing            missing      268   
578       missing          missing  missing            missing      268   
587       missing          missing  missing            missing      268   

    program_id model_props_id   symbol  
485          1           1897  Diglett  
562          1           1899  Persian  
569          1           1900  Psyduck  
578          1           1896  Rattata  
587          1           1898  Dugtrio

In [42]:
combined_df[combined_df.FUNDID=='MedichamMega Medicham']

PLANID PLANINVCLOSEDATE                 FUNDID partner_program_id  \
424  VW0029000243       01/15/2019  MedichamMega Medicham                 29   
495  VWPALL000076       01/15/2019  MedichamMega Medicham                  1   

    model_id program_id model_props_id   symbol  
424  missing    missing        missing  missing  
495  missing    missing        missing  missing

In [43]:
combined_df[combined_df.FUNDID=='ManectricMega Manectric']

PLANID PLANINVCLOSEDATE                   FUNDID  \
505  VWPALL000076           active  ManectricMega Manectric   

    partner_program_id model_id program_id model_props_id   symbol  
505                  1  missing    missing        missing  missing

### Group and combine

In [44]:
df1 =combined_df.groupby(['partner_program_id','program_id','model_id'])['FUNDID'].apply(','.join).reset_index()

In [45]:
df2 = combined_df.groupby(['partner_program_id','program_id','model_id'])['symbol'].apply(','.join).reset_index()

In [46]:
df1

partner_program_id program_id model_id  \
0                    1          1      260   
1                    1          1      261   
2                    1          1      262   
3                    1          1      263   
4                    1          1      264   
..                 ...        ...      ...   
212            missing         29      352   
213            missing         29      353   
214            missing         29      354   
215            missing         29      355   
216            missing         29      356   

                                                FUNDID  
0                                      Diglett,Torchic  
1                                              Diglett  
2                                              Diglett  
3                                              Diglett  
4                                              Diglett  
..                                                 ...  
212    missing,missing,missing,missing,missing,missing  
213    missing,missing,missing,missing,missing,missing  
214    missing,missing,missing,missing,missing,missing  
215  missing,missing,missing,missing,missing,missin...  
216            missing,missing,missing,missing,missing  

[217 rows x 4 columns]

In [47]:
df2

partner_program_id program_id model_id  \
0                    1          1      260   
1                    1          1      261   
2                    1          1      262   
3                    1          1      263   
4                    1          1      264   
..                 ...        ...      ...   
212            missing         29      352   
213            missing         29      353   
214            missing         29      354   
215            missing         29      355   
216            missing         29      356   

                                                symbol  
0                                      Diglett,Torchic  
1                                              Diglett  
2                                              Diglett  
3                                              Diglett  
4                                              Diglett  
..                                                 ...  
212       Rattata,Dugtrio,Psyduck,Persian,Paras,Phanpy  
213       Rattata,Dugtrio,Psyduck,Persian,Paras,Phanpy  
214       Rattata,Psyduck,Paras,Venonat,Phanpy,Donphan  
215  Rattata,Dugtrio,Psyduck,Paras,Venonat,Phanpy,P...  
216              Paras,Venonat,Phanpy,Donphan,Porygon2  

[217 rows x 4 columns]

In [48]:
c_df = pd.merge(df1, df2,  how='outer',on=['partner_program_id','program_id','model_id'])

In [51]:
c_df

partner_program_id program_id model_id  \
0                    1          1      260   
1                    1          1      261   
2                    1          1      262   
3                    1          1      263   
4                    1          1      264   
5                    1          1      265   
6                    1          1      266   
7                    1          1      267   
8                    1          1      268   
9                    1          1      269   
10                   1    missing  missing   
11                   8          8       53   
12                   8          8       54   
13                   8          8       55   
14                   8          8       56   
15                   8          8       57   
16                   8          8       58   
17                   8          8       59   
18                   8          8       60   
19                   8          8       61   
20                   8          8       62   
21                   8          8       63   
22                   8          8       64   
23                   8          8       65   
24                   8    missing  missing   
25                   9          9       66   
26                   9          9       67   
27                   9          9       68   
28                   9          9       69   
29                   9          9       70   
30                   9          9       71   
31                   9          9       72   
32                   9          9       73   
33                   9          9       74   
34                   9          9       75   
35                   9    missing  missing   
36                  10         10       80   
37                  12         12       81   
38                  12         12       82   
39                  12         12       83   
40                  12         12       84   
41                  12         12       85   
42                  12         12       86   
43                  12         12       87   
44                  12         12       88   
45                  12         12       89   
46                  12         12       90   
47                  12         12       91   
48                  12         12       92   
49                  12         12       93   
50                  13         13       94   
51                  13         13       95   
52                  13         13       96   
53                  13         13       97   
54                  13         13       98   
55                  13         13       99   
56                  13         13      100   
57                  13         13      101   
58                  13         13      102   
59                  13         13      103   
60                  14         14      113   
61                  15         15      151   
62                  15         15      152   
63                  15         15      153   
64                  15         15      154   
65                  15         15      155   
66                  15         15      156   
67                  15         15      157   
68                  15         15      158   
69                  15         15      159   
70                  15         15      160   
71                  15         15      161   
72                  15         15      162   
73                  15         15      163   
74                  15    missing  missing   
75                  16         16      188   
76                  17         17      183   
77                  19         19      194   
78                  19         19      195   
79                  19         19      196   
80                  19         19      197   
81                  19         19      202   
82                  20         20      205   
83                  20         20      206   
84                  20         20      207   
85                  20         20      208   
86

### Make Output_df

#### Create frame for baseline for output_df

In [52]:
#will create output df with every unique program_id and model_id combination
output_df_1 = c_df.groupby(['program_id','model_id']).size().reset_index()

In [55]:
output_df_1

program_id model_id  0
0            1      259  1
1            1      260  2
2            1      261  2
3            1      262  2
4            1      263  2
5            1      264  2
6            1      265  2
7            1      266  2
8            1      267  2
9            1      268  2
10           1      269  1
11           3       17  1
12           3       18  1
13           3       19  1
14           3       20  1
15           3       21  1
16           3       22  1
17           3       23  1
18           3       24  1
19           3       28  1
20           4       29  1
21           4       30  1
22           4       31  1
23           4       32  1
24           4       33  1
25           4       34  1
26           4       42  1
27           8       53  1
28           8       54  1
29           8       55  1
30           8       56  1
31           8       57  1
32           8       58  1
33           8       59  1
34           8       60  1
35           8       61  1
36           8       62  1
37           8       63  1
38           8       64  1
39           8       65  1
40           9       66  1
41           9       67  1
42           9       68  1
43           9       69  1
44           9       70  1
45           9       71  1
46           9       72  1
47           9       73  1
48           9       74  1
49           9       75  1
50          10       80  1
51          11      104  1
52          11      105  1
53          11      106  1
54          11      107  1
55          11      108  1
56          11      109  1
57          11      110  1
58          11      111  1
59          11      112  1
60          12       81  1
61          12       82  1
62          12       83  1
63          12       84  1
64          12       85  1
65          12       86  1
66          12       87  1
67          12       88  1
68          12       89  1
69          12       90  1
70          12       91  1
71          12       92  1
72          12       93  1
73          13       94  1
74          13       95  1
75          13       96  1
76          13       97  1
77          13       98  1
78          13       99  1
79          13      100  1
80          13      101  1
81          13      102  1
82          13      103  1
83          14      113  1
84          15      151  1
85          15      152  1
86          15      153  1
87          15      154  1
88          15      155  1
89          15      156  1
90          15      157  1
91          15      158  1
92          15      159  1
93          15      160  1
94          15      161  1
95          15      162  1
96          15      163  1
97          16      188  2
98          17      183  1
99          19      194  1
100         19      195  1
101         19      196  1
102         19      197  1
103         19      202  1
104         20      205  1
105         20      206  1
106         20      207  1
107         20      208  1
108         20      209  1
109         20      210  1
110         20      211  1
111         20      212  1
112         20      213  1
113         20      214  1
114         21      236  1
115         21      237  1
116         21      238  1
117         21      239  1
118         21      240  1
119         21      241  1
120         21      242  1
121         21      243  1
122         21      244  1
123         21      245  1
124         21      246  1
125         21      247  1
126         22      223  1
127         22      224  1
128         22      225  1
129         22      226  1
130         22      227  1
131         22      228  1
132         22      229  1
133         22      230  1
134         22      231  1
135         22      232  1
136         22      233  1
137         22      234  1
138         22      235  1
139         24      273  2
140         26      275  1
141         26      276  1
142         26      277  1
143         26      278  1
144         26      279  1
145         26      280  1
146         26      281  1
147     

In [56]:
output_df_1.drop(index=output_df_1[output_df_1.program_id=='missing'].index,inplace=True)

#### Assign initial funds_missing_at_partner column (part 1)

In [57]:
idx = c_df.loc[c_df.partner_program_id =='missing'].index
output_df_2 = c_df.loc[idx, ['program_id', 'model_id', 'symbol']]
output_df_2.rename(columns={"symbol": "funds_missing_at_partner"}, inplace=True)

In [58]:
output_df_2

program_id model_id  \
146          1      259   
147          1      260   
148          1      261   
149          1      262   
150          1      263   
151          1      264   
152          1      265   
153          1      266   
154          1      267   
155          1      268   
156          3       17   
157          3       18   
158          3       19   
159          3       20   
160          3       21   
161          3       22   
162          3       23   
163          3       24   
164          3       28   
165          4       29   
166          4       30   
167          4       31   
168          4       32   
169          4       33   
170          4       34   
171          4       42   
172         11      104   
173         11      105   
174         11      106   
175         11      107   
176         11      108   
177         11      109   
178         11      110   
179         11      111   
180         11      112   
181         16      188   
182         22      223   
183         22      224   
184         22      225   
185         22      226   
186         22      227   
187         22      228   
188         22      229   
189         22      230   
190         22      231   
191         22      232   
192         22      233   
193         22      234   
194         22      235   
195         24      273   
196         26      275   
197         26      276   
198         26      277   
199         26      278   
200         26      279   
201         26      280   
202         26      281   
203         26      282   
204         26      283   
205         26      284   
206         27      336   
207         29      347   
208         29      348   
209         29      349   
210         29      350   
211         29      351   
212         29      352   
213         29      353   
214         29      354   
215         29      355   
216         29      356   

                                                                                                                                                                                                                      funds_missing_at_partner  
146                                                                                                                                                                                                      Paras,Phanpy,Venonat,Donphan,Porygon2  
147                                                                                                                                                                                               Psyduck,Rattata,Paras,Phanpy,Venonat,Donphan  
148                                                                                                                                                                                      Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat,Porygon2  
149                                                                                                                                                                                       Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat  
150                                                                                                                                                                                               Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy  
151                                                                                                                                                                                               Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy  
152                                                                                                                                                                                               Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy  
153                                                                                                                                

#### Join values to baseline output_df

In [59]:
#left join keeps all the unique program_id & model_id combinations from output_df_1
output_df = pd.merge(output_df_1, output_df_2, how='left', left_on=['program_id','model_id'], 
                     right_on = ['program_id','model_id'])
output_df.drop(columns=[0], inplace=True)

In [60]:
output_df

program_id model_id  \
0            1      259   
1            1      260   
2            1      261   
3            1      262   
4            1      263   
5            1      264   
6            1      265   
7            1      266   
8            1      267   
9            1      268   
10           1      269   
11           3       17   
12           3       18   
13           3       19   
14           3       20   
15           3       21   
16           3       22   
17           3       23   
18           3       24   
19           3       28   
20           4       29   
21           4       30   
22           4       31   
23           4       32   
24           4       33   
25           4       34   
26           4       42   
27           8       53   
28           8       54   
29           8       55   
30           8       56   
31           8       57   
32           8       58   
33           8       59   
34           8       60   
35           8       61   
36           8       62   
37           8       63   
38           8       64   
39           8       65   
40           9       66   
41           9       67   
42           9       68   
43           9       69   
44           9       70   
45           9       71   
46           9       72   
47           9       73   
48           9       74   
49           9       75   
50          10       80   
51          11      104   
52          11      105   
53          11      106   
54          11      107   
55          11      108   
56          11      109   
57          11      110   
58          11      111   
59          11      112   
60          12       81   
61          12       82   
62          12       83   
63          12       84   
64          12       85   
65          12       86   
66          12       87   
67          12       88   
68          12       89   
69          12       90   
70          12       91   
71          12       92   
72          12       93   
73          13       94   
74          13       95   
75          13       96   
76          13       97   
77          13       98   
78          13       99   
79          13      100   
80          13      101   
81          13      102   
82          13      103   
83          14      113   
84          15      151   
85          15      152   
86          15      153   
87          15      154   
88          15      155   
89          15      156   
90          15      157   
91          15      158   
92          15      159   
93          15      160   
94          15      161   
95          15      162   
96          15      163   
97          16      188   
98          17      183   
99          19      194   
100         19      195   
101         19      196   
102         19      197   
103         19      202   
104         20      205   
105         20      206   
106         20      207   
107         20      208   
108         20      209   
109         20      210   
110         20      211   
111         20      212   
112         20      213   
113         20      214   
114         21      236   
115         21      237   
116         21      238   
117         21      239   
118         21      240   
119         21      241   
120         21      242   
121         21      243   
122         21      244   
123         21      245   
124         21      246   
125         21      247   
126         22      223   
127         22      224   
128         22      225   
129         22      226   
130         22      227   
131         22      228   
132         22      229   
133         22      230   
134         22      231   
135         22      232   
136         22      233   
137         22      234   
138         22      235   
139         24      273   
140         26      275   
141         26      276   
142         26      277   
143         26      278   
144         26      279   
145         26      280   
146         26      281   
147     

#### Assign funds_missing_at_partner column (part 2) 
- edge case where partner_program_id db is completely missing a vw program_id

In [61]:
#gets list of program_id completely missing in partner.partner_program_id db
missing_program_id_partner = []
for i in c_df.program_id.unique():
    if i not in c_df.partner_program_id.unique():
        missing_program_id_partner.append(i)

In [65]:
combined_df[combined_df.partner_program_id==3]

Empty DataFrame
Columns: [PLANID, PLANINVCLOSEDATE, FUNDID, partner_program_id, model_id, program_id, model_props_id, symbol]
Index: []

In [62]:
missing_program_id_partner

[3.0, 4.0, 11.0, 22.0, 26.0]

In [66]:
for miss_id in missing_program_id_partner:
    funds = []
    for item in output_df[output_df.program_id == miss_id].funds_missing_at_partner.values:
        try:
            funds.extend(item.split(','))
        except:
            funds.extend(item)
    #assign set of funds to all program_ids at current missing_id
    idx = output_df[output_df.program_id == miss_id].funds_missing_at_partner.index
    for index in idx:
        output_df.at[idx, 'funds_missing_at_partner'] = set(funds)

In [67]:
output_df[output_df.program_id == 3]#.funds_missing_at_partner

program_id model_id  \
11          3       17   
12          3       18   
13          3       19   
14          3       20   
15          3       21   
16          3       22   
17          3       23   
18          3       24   
19          3       28   

                                                                                                             funds_missing_at_partner  
11  {Weedle, Pidgeotto, PidgeotMega Pidgeot, Butterfree, BeedrillMega Beedrill, Pidgeot, Kakuna, Beedrill, Metapod, Pidgey, Caterpie}  
12  {Weedle, Pidgeotto, PidgeotMega Pidgeot, Butterfree, BeedrillMega Beedrill, Pidgeot, Kakuna, Beedrill, Metapod, Pidgey, Caterpie}  
13  {Weedle, Pidgeotto, PidgeotMega Pidgeot, Butterfree, BeedrillMega Beedrill, Pidgeot, Kakuna, Beedrill, Metapod, Pidgey, Caterpie}  
14  {Weedle, Pidgeotto, PidgeotMega Pidgeot, Butterfree, BeedrillMega Beedrill, Pidgeot, Kakuna, Beedrill, Metapod, Pidgey, Caterpie}  
15  {Weedle, Pidgeotto, PidgeotMega Pidgeot, Butterfree, BeedrillMega Beedrill, Pidgeot, Kakuna, Beedrill, Metapod, Pidgey, Caterpie}  
16  {Weedle, Pidgeotto, PidgeotMega Pidgeot, Butterfree, BeedrillMega Beedrill, Pidgeot, Kakuna, Beedrill, Metapod, Pidgey, Caterpie}  
17  {Weedle, Pidgeotto, PidgeotMega Pidgeot, Butterfree, BeedrillMega Beedrill, Pidgeot, Kakuna, Beedrill, Metapod, Pidgey, Caterpie}  
18  {Weedle, Pidgeotto, PidgeotMega Pidgeot, Butterfree, BeedrillMega Beedrill, Pidgeot, Kakuna, Beedrill, Metapod, Pidgey, Caterpie}  
19  {Weedle, Pidgeotto, PidgeotMega Pidgeot, Butterfree, BeedrillMega Beedrill, Pidgeot, Kakuna, Beedrill, Metapod, Pidgey, Caterpie}

#### Create and assign funds_missing_at_vw column (part 1)

##### Initial assignment
get each (partner_program_id & FUNDID) where (program_id!='missing')

In [68]:
missing_vw = c_df.loc[c_df.loc[c_df.program_id =='missing'].index, 
                      ['partner_program_id', 'FUNDID']].set_index('partner_program_id')

In [69]:
#function gets a program_id and  if missing_vw.at[partner_program_id, 'FUNDID'] exists
# it assigns the missing FUNDIDS the that program_id
def pop_missing_at_vw_part_one(partner_program_id):
    #if this program_id has missing FUNDS
    try:
        return missing_vw.at[partner_program_id, 'FUNDID']
    #else keep it empty for now
    except:
        return np.nan

In [70]:
missing_vw

FUNDID
partner_program_id                                                                                                                      
1.0                                                                              MedichamMega Medicham,Manectric,ManectricMega Manectric
8.0                                                                                                                             Carvanha
9.0                                                                                                                             Sharpedo
15.0                Charmander,SharpedoMega Sharpedo,CharizardMega Charizard Y,BlastoiseMega Blastoise,CharizardMega Charizard X,Wailmer
24.0                                                                                                                             Wailord
27.0                                                                                                                     Plusle,Sharpedo
28.0                                                                                                                    Bulbasaur,Plusle
29.0                                               MedichamMega Medicham,Minun,Volbeat,Illumise,Venomoth,Roselia,Parasect,Golduck,Gulpin
30.0                                                                                                                               Numel

In [71]:
#assign the missing FUNDIDS to all program_ids
output_df['funds_missing_at_vw'] = output_df.program_id.apply(pop_missing_at_vw_part_one)

In [72]:
output_df

program_id model_id  \
0            1      259   
1            1      260   
2            1      261   
3            1      262   
4            1      263   
5            1      264   
6            1      265   
7            1      266   
8            1      267   
9            1      268   
10           1      269   
11           3       17   
12           3       18   
13           3       19   
14           3       20   
15           3       21   
16           3       22   
17           3       23   
18           3       24   
19           3       28   
20           4       29   
21           4       30   
22           4       31   
23           4       32   
24           4       33   
25           4       34   
26           4       42   
27           8       53   
28           8       54   
29           8       55   
30           8       56   
31           8       57   
32           8       58   
33           8       59   
34           8       60   
35           8       61   
36           8       62   
37           8       63   
38           8       64   
39           8       65   
40           9       66   
41           9       67   
42           9       68   
43           9       69   
44           9       70   
45           9       71   
46           9       72   
47           9       73   
48           9       74   
49           9       75   
50          10       80   
51          11      104   
52          11      105   
53          11      106   
54          11      107   
55          11      108   
56          11      109   
57          11      110   
58          11      111   
59          11      112   
60          12       81   
61          12       82   
62          12       83   
63          12       84   
64          12       85   
65          12       86   
66          12       87   
67          12       88   
68          12       89   
69          12       90   
70          12       91   
71          12       92   
72          12       93   
73          13       94   
74          13       95   
75          13       96   
76          13       97   
77          13       98   
78          13       99   
79          13      100   
80          13      101   
81          13      102   
82          13      103   
83          14      113   
84          15      151   
85          15      152   
86          15      153   
87          15      154   
88          15      155   
89          15      156   
90          15      157   
91          15      158   
92          15      159   
93          15      160   
94          15      161   
95          15      162   
96          15      163   
97          16      188   
98          17      183   
99          19      194   
100         19      195   
101         19      196   
102         19      197   
103         19      202   
104         20      205   
105         20      206   
106         20      207   
107         20      208   
108         20      209   
109         20      210   
110         20      211   
111         20      212   
112         20      213   
113         20      214   
114         21      236   
115         21      237   
116         21      238   
117         21      239   
118         21      240   
119         21      241   
120         21      242   
121         21      243   
122         21      244   
123         21      245   
124         21      246   
125         21      247   
126         22      223   
127         22      224   
128         22      225   
129         22      226   
130         22      227   
131         22      228   
132         22      229   
133         22      230   
134         22      231   
135         22      232   
136         22      233   
137         22      234   
138         22      235   
139         24      273   
140         26      275   
141         26      276   
142         26      277   
143         26      278   
144         26      279   
145         26      280   
146         26      281   
147     

In [ ]:
# c_df.loc[c_df.program_id =='missing'].index

In [ ]:
# c_df.loc[c_df.program_id =='missing']

##### Complete Population across all (part 2)

In [73]:
c_df

partner_program_id program_id model_id  \
0                    1          1      260   
1                    1          1      261   
2                    1          1      262   
3                    1          1      263   
4                    1          1      264   
5                    1          1      265   
6                    1          1      266   
7                    1          1      267   
8                    1          1      268   
9                    1          1      269   
10                   1    missing  missing   
11                   8          8       53   
12                   8          8       54   
13                   8          8       55   
14                   8          8       56   
15                   8          8       57   
16                   8          8       58   
17                   8          8       59   
18                   8          8       60   
19                   8          8       61   
20                   8          8       62   
21                   8          8       63   
22                   8          8       64   
23                   8          8       65   
24                   8    missing  missing   
25                   9          9       66   
26                   9          9       67   
27                   9          9       68   
28                   9          9       69   
29                   9          9       70   
30                   9          9       71   
31                   9          9       72   
32                   9          9       73   
33                   9          9       74   
34                   9          9       75   
35                   9    missing  missing   
36                  10         10       80   
37                  12         12       81   
38                  12         12       82   
39                  12         12       83   
40                  12         12       84   
41                  12         12       85   
42                  12         12       86   
43                  12         12       87   
44                  12         12       88   
45                  12         12       89   
46                  12         12       90   
47                  12         12       91   
48                  12         12       92   
49                  12         12       93   
50                  13         13       94   
51                  13         13       95   
52                  13         13       96   
53                  13         13       97   
54                  13         13       98   
55                  13         13       99   
56                  13         13      100   
57                  13         13      101   
58                  13         13      102   
59                  13         13      103   
60                  14         14      113   
61                  15         15      151   
62                  15         15      152   
63                  15         15      153   
64                  15         15      154   
65                  15         15      155   
66                  15         15      156   
67                  15         15      157   
68                  15         15      158   
69                  15         15      159   
70                  15         15      160   
71                  15         15      161   
72                  15         15      162   
73                  15         15      163   
74                  15    missing  missing   
75                  16         16      188   
76                  17         17      183   
77                  19         19      194   
78                  19         19      195   
79                  19         19      196   
80                  19         19      197   
81                  19         19      202   
82                  20         20      205   
83                  20         20      206   
84                  20         20      207   
85                  20         20      208   
86

##### Create agg_fund lists for each unique program_id & partner_program_id pairs
we ignore columns with 'missing' valuesby replacing with nan

In [74]:
remainder_groupby = c_df.replace({'missing': np.nan}).groupby(['partner_program_id',
                                                               'program_id'])['FUNDID'].apply(','.join).reset_index()


In [75]:
remainder_groupby.rename(columns={"FUNDID": "fund_agg"}, inplace=True)
remainder_groupby.fund_agg = remainder_groupby.fund_agg.apply(lambda x: set(x.split(',')))
remainder_groupby

partner_program_id  program_id  \
0                  1.0         1.0   
1                  8.0         8.0   
2                  9.0         9.0   
3                 10.0        10.0   
4                 12.0        12.0   
5                 13.0        13.0   
6                 14.0        14.0   
7                 15.0        15.0   
8                 16.0        16.0   
9                 17.0        17.0   
10                19.0        19.0   
11                20.0        20.0   
12                21.0        21.0   
13                24.0        24.0   
14                27.0        27.0   
15                28.0        28.0   
16                29.0        29.0   
17                30.0        30.0   

                                                                                                                                                                                                                                                                                                                                                                                                            fund_agg  
0                                                                                                                                                                                                                                                                                          {Growlithe, Torchic, Teddiursa, Tyrogue, Stantler, Hitmontop, Xatu, Gastly, Sneasel, Meowth, Diglett, Smoochum, Smeargle}  
1                                                                                                                        {Arbok, Nidorina, Spearow, Primeape, Golbat, Nidoqueen, Ninetales, Sandslash, Nidoking, Zubat, Raticate, CharizardMega Charizard X, Nidorino, Vulpix, Clefairy, Arcanine, Vileplume, Ekans, Fearow, Wigglytuff, Gloom, Clefable, Sandshrew, Growlithe, Pikachu, Jigglypuff, Raichu, Oddish}  
2                 {Rapidash, Weepinbell, BlastoiseMega Blastoise, Charmander, Magneton, Machoke, Poliwhirl, SlowbroMega Slowbro, Geodude, Poliwrath, Poliwag, Magnemite, Zubat, Slowbro, Ponyta, Doduo, Tentacool, Venusaur, Tentacruel, Golem, Graveler, Blastoise, VenusaurMega Venusaur, Squirtle, Slowpoke, Machop, Alakazam, Machamp, Farfetch'd, Abra, Bellsprout, Victreebel, Kadabra, AlakazamMega Alakazam}  
3                                                                                                                                                                                                            {Venusaur, Bulbasaur, BlastoiseMega Blastoise, Charmander, Blastoise, VenusaurMega Venusaur, Ivysaur, Squirtle, CharizardMega Charizard Y, Charizard, Wartortle, CharizardMega Charizard X, Charmeleon}  
4                                                                                    {Rapidash, BlastoiseMega Blastoise, Dodrio, Charmander, CharizardMega Charizard Y, Magneton, Seel, SlowbroMega Slowbro, Magnemite, Slowbro, Grimer, Ponyta, CharizardMega Charizard X, Doduo, Shellder, Dewgong, Golem, Blastoise, VenusaurMega Venusaur, Squirtle, Slowpoke, Charmeleon, Cloyster, Muk, Farfetch'd, Charizard}  
5                                                                                                                                            {Rapidash, Rhyhorn, Haunter, Koffing, Magneton, SlowbroMega Slowbro, Geodude, Magnemite, Slowbro, Ponyta, CharizardMega Charizard X, Doduo, Hitmonlee, Marowak, Hitmonchan, Voltorb, Slowpoke, Exeggcute, Farfetch'd, Weezing, Lickitung, Electrode, Cubone, Exeggutor}  
6                                                                                                                                               {Bulbasaur, Quilava, Charmander, Mew, Meganium, Dragonite, Aerodactyl, Articuno, Chikorita, Zapdos, Cyndaquil, Vulpix, Mewtwo, Snorlax, AerodactylMega Aerodactyl, Magikarp, Bayleef, Dragonair, MewtwoMega Mewtwo Y, MewtwoMega Mewtwo X, Gastly, Moltres, Dratini}  
7                        

In [80]:
# cast to allow merge with c_df
remainder_groupby=remainder_groupby.astype({'partner_program_id': 'object','program_id': 'object'})

In [81]:
# c_df.astype({'partner_program_id': 'float','program_id': 'float'})

In [82]:
remainder_groupby.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18 entries, 0 to 17
Data columns (total 3 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   partner_program_id  18 non-null     object
 1   program_id          18 non-null     object
 2   fund_agg            18 non-null     object
dtypes: object(3)
memory usage: 560.0+ bytes


In [83]:
c_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 217 entries, 0 to 216
Data columns (total 5 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   partner_program_id  217 non-null    object
 1   program_id          217 non-null    object
 2   model_id            217 non-null    object
 3   FUNDID              217 non-null    object
 4   symbol              217 non-null    object
dtypes: object(5)
memory usage: 20.2+ KB


In [84]:
missing_df = pd.merge(remainder_groupby, c_df.replace({'missing': np.nan}),how='inner',
                      left_on=['program_id', 'partner_program_id'], right_on = ['program_id', 'partner_program_id'])
missing_df.drop(columns='FUNDID',inplace=True)
# missing_df.dropna(inplace=True)

In [85]:
missing_df

partner_program_id program_id  \
0                    1          1   
1                    1          1   
2                    1          1   
3                    1          1   
4                    1          1   
5                    1          1   
6                    1          1   
7                    1          1   
8                    1          1   
9                    1          1   
10                   8          8   
11                   8          8   
12                   8          8   
13                   8          8   
14                   8          8   
15                   8          8   
16                   8          8   
17                   8          8   
18                   8          8   
19                   8          8   
20                   8          8   
21                   8          8   
22                   8          8   
23                   9          9   
24                   9          9   
25                   9          9   
26                   9          9   
27                   9          9   
28                   9          9   
29                   9          9   
30                   9          9   
31                   9          9   
32                   9          9   
33                  10         10   
34                  12         12   
35                  12         12   
36                  12         12   
37                  12         12   
38                  12         12   
39                  12         12   
40                  12         12   
41                  12         12   
42                  12         12   
43                  12         12   
44                  12         12   
45                  12         12   
46                  12         12   
47                  13         13   
48                  13         13   
49                  13         13   
50                  13         13   
51                  13         13   
52                  13         13   
53                  13         13   
54                  13         13   
55                  13         13   
56                  13         13   
57                  14         14   
58                  15         15   
59                  15         15   
60                  15         15   
61                  15         15   
62                  15         15   
63                  15         15   
64                  15         15   
65                  15         15   
66                  15         15   
67                  15         15   
68                  15         15   
69                  15         15   
70                  15         15   
71                  16         16   
72                  17         17   
73                  19         19   
74                  19         19   
75                  19         19   
76                  19         19   
77                  19         19   
78                  20         20   
79                  20         20   
80                  20         20   
81                  20         20   
82                  20         20   
83                  20         20   
84                  20         20   
85                  20         20   
86                  20         20   
87                  20         20   
88                  21         21   
89                  21         21   
90                  21         21   
91                  21         21   
92                  21         21   
93                  21         21   
94                  21         21   
95                  21         21   
96                  21         21   
97                  21         21   
98                  21         21   
99                  21         21   
100                 24         24   
101                 27         27   
102                 27         27   
103                 27         27   
104                 27         27   
105                 27         27   
106                 27         27   
107     

In [86]:
missing_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 137 entries, 0 to 136
Data columns (total 5 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   partner_program_id  137 non-null    object 
 1   program_id          137 non-null    object 
 2   fund_agg            137 non-null    object 
 3   model_id            137 non-null    float64
 4   symbol              137 non-null    object 
dtypes: float64(1), object(4)
memory usage: 6.4+ KB


In [87]:
missing_df.fund_agg = missing_df.fund_agg.apply(lambda x: list(x))

In [88]:
missing_df

partner_program_id program_id  \
0                    1          1   
1                    1          1   
2                    1          1   
3                    1          1   
4                    1          1   
5                    1          1   
6                    1          1   
7                    1          1   
8                    1          1   
9                    1          1   
10                   8          8   
11                   8          8   
12                   8          8   
13                   8          8   
14                   8          8   
15                   8          8   
16                   8          8   
17                   8          8   
18                   8          8   
19                   8          8   
20                   8          8   
21                   8          8   
22                   8          8   
23                   9          9   
24                   9          9   
25                   9          9   
26                   9          9   
27                   9          9   
28                   9          9   
29                   9          9   
30                   9          9   
31                   9          9   
32                   9          9   
33                  10         10   
34                  12         12   
35                  12         12   
36                  12         12   
37                  12         12   
38                  12         12   
39                  12         12   
40                  12         12   
41                  12         12   
42                  12         12   
43                  12         12   
44                  12         12   
45                  12         12   
46                  12         12   
47                  13         13   
48                  13         13   
49                  13         13   
50                  13         13   
51                  13         13   
52                  13         13   
53                  13         13   
54                  13         13   
55                  13         13   
56                  13         13   
57                  14         14   
58                  15         15   
59                  15         15   
60                  15         15   
61                  15         15   
62                  15         15   
63                  15         15   
64                  15         15   
65                  15         15   
66                  15         15   
67                  15         15   
68                  15         15   
69                  15         15   
70                  15         15   
71                  16         16   
72                  17         17   
73                  19         19   
74                  19         19   
75                  19         19   
76                  19         19   
77                  19         19   
78                  20         20   
79                  20         20   
80                  20         20   
81                  20         20   
82                  20         20   
83                  20         20   
84                  20         20   
85                  20         20   
86                  20         20   
87                  20         20   
88                  21         21   
89                  21         21   
90                  21         21   
91                  21         21   
92                  21         21   
93                  21         21   
94                  21         21   
95                  21         21   
96                  21         21   
97                  21         21   
98                  21         21   
99                  21         21   
100                 24         24   
101                 27         27   
102                 27         27   
103                 27         27   
104                 27         27   
105                 27         27   
106                 27         27   
107     

In [91]:
c_df

partner_program_id program_id model_id  \
0                    1          1      260   
1                    1          1      261   
2                    1          1      262   
3                    1          1      263   
4                    1          1      264   
5                    1          1      265   
6                    1          1      266   
7                    1          1      267   
8                    1          1      268   
9                    1          1      269   
10                   1    missing  missing   
11                   8          8       53   
12                   8          8       54   
13                   8          8       55   
14                   8          8       56   
15                   8          8       57   
16                   8          8       58   
17                   8          8       59   
18                   8          8       60   
19                   8          8       61   
20                   8          8       62   
21                   8          8       63   
22                   8          8       64   
23                   8          8       65   
24                   8    missing  missing   
25                   9          9       66   
26                   9          9       67   
27                   9          9       68   
28                   9          9       69   
29                   9          9       70   
30                   9          9       71   
31                   9          9       72   
32                   9          9       73   
33                   9          9       74   
34                   9          9       75   
35                   9    missing  missing   
36                  10         10       80   
37                  12         12       81   
38                  12         12       82   
39                  12         12       83   
40                  12         12       84   
41                  12         12       85   
42                  12         12       86   
43                  12         12       87   
44                  12         12       88   
45                  12         12       89   
46                  12         12       90   
47                  12         12       91   
48                  12         12       92   
49                  12         12       93   
50                  13         13       94   
51                  13         13       95   
52                  13         13       96   
53                  13         13       97   
54                  13         13       98   
55                  13         13       99   
56                  13         13      100   
57                  13         13      101   
58                  13         13      102   
59                  13         13      103   
60                  14         14      113   
61                  15         15      151   
62                  15         15      152   
63                  15         15      153   
64                  15         15      154   
65                  15         15      155   
66                  15         15      156   
67                  15         15      157   
68                  15         15      158   
69                  15         15      159   
70                  15         15      160   
71                  15         15      161   
72                  15         15      162   
73                  15         15      163   
74                  15    missing  missing   
75                  16         16      188   
76                  17         17      183   
77                  19         19      194   
78                  19         19      195   
79                  19         19      196   
80                  19         19      197   
81                  19         19      202   
82                  20         20      205   
83                  20         20      206   
84                  20         20      207   
85                  20         20      208   
86

In [89]:
def what_is_missing(fund_agg, symbol):
    local_fund_agg = copy.deepcopy(fund_agg)
    try:
        my_list = symbol.split(',')
    except:
        my_list = [symbol]
    for fund in my_list:
        if fund in local_fund_agg:
            local_fund_agg.remove(fund)
    return local_fund_agg

In [90]:
missing_df['missing']= missing_df.apply(lambda x: what_is_missing(x.fund_agg, x.symbol), axis=1)

# df['col_3'] = df.apply(lambda x: function(x.col_1, x.col_2), axis=1)

In [92]:
missing_df

partner_program_id program_id  \
0                    1          1   
1                    1          1   
2                    1          1   
3                    1          1   
4                    1          1   
5                    1          1   
6                    1          1   
7                    1          1   
8                    1          1   
9                    1          1   
10                   8          8   
11                   8          8   
12                   8          8   
13                   8          8   
14                   8          8   
15                   8          8   
16                   8          8   
17                   8          8   
18                   8          8   
19                   8          8   
20                   8          8   
21                   8          8   
22                   8          8   
23                   9          9   
24                   9          9   
25                   9          9   
26                   9          9   
27                   9          9   
28                   9          9   
29                   9          9   
30                   9          9   
31                   9          9   
32                   9          9   
33                  10         10   
34                  12         12   
35                  12         12   
36                  12         12   
37                  12         12   
38                  12         12   
39                  12         12   
40                  12         12   
41                  12         12   
42                  12         12   
43                  12         12   
44                  12         12   
45                  12         12   
46                  12         12   
47                  13         13   
48                  13         13   
49                  13         13   
50                  13         13   
51                  13         13   
52                  13         13   
53                  13         13   
54                  13         13   
55                  13         13   
56                  13         13   
57                  14         14   
58                  15         15   
59                  15         15   
60                  15         15   
61                  15         15   
62                  15         15   
63                  15         15   
64                  15         15   
65                  15         15   
66                  15         15   
67                  15         15   
68                  15         15   
69                  15         15   
70                  15         15   
71                  16         16   
72                  17         17   
73                  19         19   
74                  19         19   
75                  19         19   
76                  19         19   
77                  19         19   
78                  20         20   
79                  20         20   
80                  20         20   
81                  20         20   
82                  20         20   
83                  20         20   
84                  20         20   
85                  20         20   
86                  20         20   
87                  20         20   
88                  21         21   
89                  21         21   
90                  21         21   
91                  21         21   
92                  21         21   
93                  21         21   
94                  21         21   
95                  21         21   
96                  21         21   
97                  21         21   
98                  21         21   
99                  21         21   
100                 24         24   
101                 27         27   
102                 27         27   
103                 27         27   
104                 27         27   
105                 27         27   
106                 27         27   
107     

#### Now combine with output df

In [94]:
missing_df = missing_df.astype({'model_id': 'object', 'program_id': 'object'})

In [95]:
missing_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 137 entries, 0 to 136
Data columns (total 6 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   partner_program_id  137 non-null    object
 1   program_id          137 non-null    object
 2   fund_agg            137 non-null    object
 3   model_id            137 non-null    object
 4   symbol              137 non-null    object
 5   missing             137 non-null    object
dtypes: object(6)
memory usage: 7.5+ KB


In [96]:
output_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 187 entries, 0 to 186
Data columns (total 4 columns):
 #   Column                    Non-Null Count  Dtype 
---  ------                    --------------  ----- 
 0   program_id                187 non-null    object
 1   model_id                  187 non-null    object
 2   funds_missing_at_partner  71 non-null     object
 3   funds_missing_at_vw       85 non-null     object
dtypes: object(4)
memory usage: 12.3+ KB


In [97]:
output_final = pd.merge(output_df, missing_df,  how='outer',left_on=['program_id', 'model_id'], 
                     right_on = ['program_id', 'model_id'])

In [98]:
output_final 

program_id model_id  \
0            1      259   
1            1      260   
2            1      261   
3            1      262   
4            1      263   
5            1      264   
6            1      265   
7            1      266   
8            1      267   
9            1      268   
10           1      269   
11           3       17   
12           3       18   
13           3       19   
14           3       20   
15           3       21   
16           3       22   
17           3       23   
18           3       24   
19           3       28   
20           4       29   
21           4       30   
22           4       31   
23           4       32   
24           4       33   
25           4       34   
26           4       42   
27           8       53   
28           8       54   
29           8       55   
30           8       56   
31           8       57   
32           8       58   
33           8       59   
34           8       60   
35           8       61   
36           8       62   
37           8       63   
38           8       64   
39           8       65   
40           9       66   
41           9       67   
42           9       68   
43           9       69   
44           9       70   
45           9       71   
46           9       72   
47           9       73   
48           9       74   
49           9       75   
50          10       80   
51          11      104   
52          11      105   
53          11      106   
54          11      107   
55          11      108   
56          11      109   
57          11      110   
58          11      111   
59          11      112   
60          12       81   
61          12       82   
62          12       83   
63          12       84   
64          12       85   
65          12       86   
66          12       87   
67          12       88   
68          12       89   
69          12       90   
70          12       91   
71          12       92   
72          12       93   
73          13       94   
74          13       95   
75          13       96   
76          13       97   
77          13       98   
78          13       99   
79          13      100   
80          13      101   
81          13      102   
82          13      103   
83          14      113   
84          15      151   
85          15      152   
86          15      153   
87          15      154   
88          15      155   
89          15      156   
90          15      157   
91          15      158   
92          15      159   
93          15      160   
94          15      161   
95          15      162   
96          15      163   
97          16      188   
98          17      183   
99          19      194   
100         19      195   
101         19      196   
102         19      197   
103         19      202   
104         20      205   
105         20      206   
106         20      207   
107         20      208   
108         20      209   
109         20      210   
110         20      211   
111         20      212   
112         20      213   
113         20      214   
114         21      236   
115         21      237   
116         21      238   
117         21      239   
118         21      240   
119         21      241   
120         21      242   
121         21      243   
122         21      244   
123         21      245   
124         21      246   
125         21      247   
126         22      223   
127         22      224   
128         22      225   
129         22      226   
130         22      227   
131         22      228   
132         22      229   
133         22      230   
134         22      231   
135         22      232   
136         22      233   
137         22      234   
138         22      235   
139         24      273   
140         26      275   
141         26      276   
142         26      277   
143         26      278   
144         26      279   
145         26      280   
146         26      281   
147     

In [99]:
#use remainder_groupby to populate missing fund_agg cells in output final
remainder_groupby.set_index('partner_program_id', inplace=True)
remainder_groupby

program_id  \
partner_program_id              
1.0                         1   
8.0                         8   
9.0                         9   
10.0                       10   
12.0                       12   
13.0                       13   
14.0                       14   
15.0                       15   
16.0                       16   
17.0                       17   
19.0                       19   
20.0                       20   
21.0                       21   
24.0                       24   
27.0                       27   
28.0                       28   
29.0                       29   
30.0                       30   

                                                                                                                                                                                                                                                                                                                                                                                                                            fund_agg  
partner_program_id                                                                                                                                                                                                                                                                                                                                                                                                                    
1.0                                                                                                                                                                                                                                                                                                        {Growlithe, Torchic, Teddiursa, Tyrogue, Stantler, Hitmontop, Xatu, Gastly, Sneasel, Meowth, Diglett, Smoochum, Smeargle}  
8.0                                                                                                                                      {Arbok, Nidorina, Spearow, Primeape, Golbat, Nidoqueen, Ninetales, Sandslash, Nidoking, Zubat, Raticate, CharizardMega Charizard X, Nidorino, Vulpix, Clefairy, Arcanine, Vileplume, Ekans, Fearow, Wigglytuff, Gloom, Clefable, Sandshrew, Growlithe, Pikachu, Jigglypuff, Raichu, Oddish}  
9.0                               {Rapidash, Weepinbell, BlastoiseMega Blastoise, Charmander, Magneton, Machoke, Poliwhirl, SlowbroMega Slowbro, Geodude, Poliwrath, Poliwag, Magnemite, Zubat, Slowbro, Ponyta, Doduo, Tentacool, Venusaur, Tentacruel, Golem, Graveler, Blastoise, VenusaurMega Venusaur, Squirtle, Slowpoke, Machop, Alakazam, Machamp, Farfetch'd, Abra, Bellsprout, Victreebel, Kadabra, AlakazamMega Alakazam}  
10.0                                                                                                                                                                                                                         {Venusaur, Bulbasaur, BlastoiseMega Blastoise, Charmander, Blastoise, VenusaurMega Venusaur, Ivysaur, Squirtle, CharizardMega Charizard Y, Charizard, Wartortle, CharizardMega Charizard X, Charmeleon}  
12.0                                                                                                 {Rapidash, BlastoiseMega Blastoise, Dodrio, Charmander, CharizardMega Charizard Y, Magneton, Seel, SlowbroMega Slowbro, Magnemite, Slowbro, Grimer, Ponyta, CharizardMega Charizard X, Doduo, Shellder, Dewgong, Golem, Blastoise, VenusaurMega Venusaur, Squirtle, Slowpoke, Charmeleon, Cloyster, Muk, Farfetch'd, Charizard}  
13.0                                                                                                                                                         {Rapidash, Rhyhorn, Haunter, Koffing, Magneton, SlowbroMega Slowbro, Geodude, Magnemite, Slowbro, Ponyta, CharizardMega Charizard X, Doduo, Hitmonlee, Marowak, Hitmonchan, Voltorb, Slowpoke, Exeggcute, Farfetch'd, Weezing, Lickitung, Electr

In [100]:
#populate NaN in the missing col
def get_missing_missing(partner_program_id, missing):
    try:
        if math.isnan(missing):
            return remainder_groupby.at[partner_program_id, 'fund_agg']
    except:
        return missing

In [101]:
output_final.missing = output_final.apply(lambda x: get_missing_missing(x.program_id, x.missing), axis=1)

In [102]:
output_final.isna().sum()

program_id                    0
model_id                      0
funds_missing_at_partner    116
funds_missing_at_vw         102
partner_program_id           50
fund_agg                     50
symbol                       50
missing                      48
dtype: int64

In [103]:
output_final

program_id model_id  \
0            1      259   
1            1      260   
2            1      261   
3            1      262   
4            1      263   
5            1      264   
6            1      265   
7            1      266   
8            1      267   
9            1      268   
10           1      269   
11           3       17   
12           3       18   
13           3       19   
14           3       20   
15           3       21   
16           3       22   
17           3       23   
18           3       24   
19           3       28   
20           4       29   
21           4       30   
22           4       31   
23           4       32   
24           4       33   
25           4       34   
26           4       42   
27           8       53   
28           8       54   
29           8       55   
30           8       56   
31           8       57   
32           8       58   
33           8       59   
34           8       60   
35           8       61   
36           8       62   
37           8       63   
38           8       64   
39           8       65   
40           9       66   
41           9       67   
42           9       68   
43           9       69   
44           9       70   
45           9       71   
46           9       72   
47           9       73   
48           9       74   
49           9       75   
50          10       80   
51          11      104   
52          11      105   
53          11      106   
54          11      107   
55          11      108   
56          11      109   
57          11      110   
58          11      111   
59          11      112   
60          12       81   
61          12       82   
62          12       83   
63          12       84   
64          12       85   
65          12       86   
66          12       87   
67          12       88   
68          12       89   
69          12       90   
70          12       91   
71          12       92   
72          12       93   
73          13       94   
74          13       95   
75          13       96   
76          13       97   
77          13       98   
78          13       99   
79          13      100   
80          13      101   
81          13      102   
82          13      103   
83          14      113   
84          15      151   
85          15      152   
86          15      153   
87          15      154   
88          15      155   
89          15      156   
90          15      157   
91          15      158   
92          15      159   
93          15      160   
94          15      161   
95          15      162   
96          15      163   
97          16      188   
98          17      183   
99          19      194   
100         19      195   
101         19      196   
102         19      197   
103         19      202   
104         20      205   
105         20      206   
106         20      207   
107         20      208   
108         20      209   
109         20      210   
110         20      211   
111         20      212   
112         20      213   
113         20      214   
114         21      236   
115         21      237   
116         21      238   
117         21      239   
118         21      240   
119         21      241   
120         21      242   
121         21      243   
122         21      244   
123         21      245   
124         21      246   
125         21      247   
126         22      223   
127         22      224   
128         22      225   
129         22      226   
130         22      227   
131         22      228   
132         22      229   
133         22      230   
134         22      231   
135         22      232   
136         22      233   
137         22      234   
138         22      235   
139         24      273   
140         26      275   
141         26      276   
142         26      277   
143         26      278   
144         26      279   
145         26      280   
146         26      281   
147     

#### Add missing column to funds_missing_at_vw and delete other columns


In [104]:
def combine_vw_missing_and_missing_col(funds_missing_at_vw, missing):
    try:
        #does 'nothing where program ids only exist at vw'
        if math.isnan(missing):
            return funds_missing_at_vw
    except:
        try:
            if math.isnan(funds_missing_at_vw):
                return ','.join(missing)
        except:
                return funds_missing_at_vw + ',' + ','.join(missing)

In [105]:
output_final.funds_missing_at_vw = output_final.apply(lambda x: combine_vw_missing_and_missing_col(x.funds_missing_at_vw, x.missing), axis=1)


In [106]:
output_final

program_id model_id  \
0            1      259   
1            1      260   
2            1      261   
3            1      262   
4            1      263   
5            1      264   
6            1      265   
7            1      266   
8            1      267   
9            1      268   
10           1      269   
11           3       17   
12           3       18   
13           3       19   
14           3       20   
15           3       21   
16           3       22   
17           3       23   
18           3       24   
19           3       28   
20           4       29   
21           4       30   
22           4       31   
23           4       32   
24           4       33   
25           4       34   
26           4       42   
27           8       53   
28           8       54   
29           8       55   
30           8       56   
31           8       57   
32           8       58   
33           8       59   
34           8       60   
35           8       61   
36           8       62   
37           8       63   
38           8       64   
39           8       65   
40           9       66   
41           9       67   
42           9       68   
43           9       69   
44           9       70   
45           9       71   
46           9       72   
47           9       73   
48           9       74   
49           9       75   
50          10       80   
51          11      104   
52          11      105   
53          11      106   
54          11      107   
55          11      108   
56          11      109   
57          11      110   
58          11      111   
59          11      112   
60          12       81   
61          12       82   
62          12       83   
63          12       84   
64          12       85   
65          12       86   
66          12       87   
67          12       88   
68          12       89   
69          12       90   
70          12       91   
71          12       92   
72          12       93   
73          13       94   
74          13       95   
75          13       96   
76          13       97   
77          13       98   
78          13       99   
79          13      100   
80          13      101   
81          13      102   
82          13      103   
83          14      113   
84          15      151   
85          15      152   
86          15      153   
87          15      154   
88          15      155   
89          15      156   
90          15      157   
91          15      158   
92          15      159   
93          15      160   
94          15      161   
95          15      162   
96          15      163   
97          16      188   
98          17      183   
99          19      194   
100         19      195   
101         19      196   
102         19      197   
103         19      202   
104         20      205   
105         20      206   
106         20      207   
107         20      208   
108         20      209   
109         20      210   
110         20      211   
111         20      212   
112         20      213   
113         20      214   
114         21      236   
115         21      237   
116         21      238   
117         21      239   
118         21      240   
119         21      241   
120         21      242   
121         21      243   
122         21      244   
123         21      245   
124         21      246   
125         21      247   
126         22      223   
127         22      224   
128         22      225   
129         22      226   
130         22      227   
131         22      228   
132         22      229   
133         22      230   
134         22      231   
135         22      232   
136         22      233   
137         22      234   
138         22      235   
139         24      273   
140         26      275   
141         26      276   
142         26      277   
143         26      278   
144         26      279   
145         26      280   
146         26      281   
147     

In [107]:
output_final.columns

Index(['program_id', 'model_id', 'funds_missing_at_partner',
       'funds_missing_at_vw', 'partner_program_id', 'fund_agg', 'symbol',
       'missing'],
      dtype='object')

In [108]:
output_final = output_final.loc[:,['program_id', 'model_id', 'funds_missing_at_partner',
       'funds_missing_at_vw']]

# Step 4 - Check for any closed funds
Check each `model_id` in each `program_id` in Vestwell's data to see if our partner has indicated a fund has closed.  We don't care about funds that have closed that aren't in Vestwell's data.  Add this information to your output from step 3.

### Add fund_missing col and populate

In [109]:
output_final

program_id model_id  \
0            1      259   
1            1      260   
2            1      261   
3            1      262   
4            1      263   
5            1      264   
6            1      265   
7            1      266   
8            1      267   
9            1      268   
10           1      269   
11           3       17   
12           3       18   
13           3       19   
14           3       20   
15           3       21   
16           3       22   
17           3       23   
18           3       24   
19           3       28   
20           4       29   
21           4       30   
22           4       31   
23           4       32   
24           4       33   
25           4       34   
26           4       42   
27           8       53   
28           8       54   
29           8       55   
30           8       56   
31           8       57   
32           8       58   
33           8       59   
34           8       60   
35           8       61   
36           8       62   
37           8       63   
38           8       64   
39           8       65   
40           9       66   
41           9       67   
42           9       68   
43           9       69   
44           9       70   
45           9       71   
46           9       72   
47           9       73   
48           9       74   
49           9       75   
50          10       80   
51          11      104   
52          11      105   
53          11      106   
54          11      107   
55          11      108   
56          11      109   
57          11      110   
58          11      111   
59          11      112   
60          12       81   
61          12       82   
62          12       83   
63          12       84   
64          12       85   
65          12       86   
66          12       87   
67          12       88   
68          12       89   
69          12       90   
70          12       91   
71          12       92   
72          12       93   
73          13       94   
74          13       95   
75          13       96   
76          13       97   
77          13       98   
78          13       99   
79          13      100   
80          13      101   
81          13      102   
82          13      103   
83          14      113   
84          15      151   
85          15      152   
86          15      153   
87          15      154   
88          15      155   
89          15      156   
90          15      157   
91          15      158   
92          15      159   
93          15      160   
94          15      161   
95          15      162   
96          15      163   
97          16      188   
98          17      183   
99          19      194   
100         19      195   
101         19      196   
102         19      197   
103         19      202   
104         20      205   
105         20      206   
106         20      207   
107         20      208   
108         20      209   
109         20      210   
110         20      211   
111         20      212   
112         20      213   
113         20      214   
114         21      236   
115         21      237   
116         21      238   
117         21      239   
118         21      240   
119         21      241   
120         21      242   
121         21      243   
122         21      244   
123         21      245   
124         21      246   
125         21      247   
126         22      223   
127         22      224   
128         22      225   
129         22      226   
130         22      227   
131         22      228   
132         22      229   
133         22      230   
134         22      231   
135         22      232   
136         22      233   
137         22      234   
138         22      235   
139         24      273   
140         26      275   
141         26      276   
142         26      277   
143         26      278   
144         26      279   
145         26      280   
146         26      281   
147     

In [110]:
# set output_df index to program_id
output_final.set_index(['program_id', 'model_id'], inplace=True)
output_final['fund_closed'] = np.empty((len(output_final), 0)).tolist()

In [111]:
output_final

funds_missing_at_partner  \
program_id model_id                                                                                                                                                                                                                                                                                                                                                              
1.0        259.0                                                                                                                                                                                                                                                                                                                         Paras,Phanpy,Venonat,Donphan,Porygon2   
           260.0                                                                                                                                                                                                                                                                                                                  Psyduck,Rattata,Paras,Phanpy,Venonat,Donphan   
           261.0                                                                                                                                                                                                                                                                                                         Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat,Porygon2   
           262.0                                                                                                                                                                                                                                                                                                          Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat   
           263.0                                                                                                                                                                                                                                                                                                                  Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           264.0                                                                                                                                                                                                                                                                                                                  Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           265.0                                                                                                                                                                                                                                                                                                                  Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           266.0                                                                                                                                                                                                                                                                                                                         Persian,Psyduck,Rattata,Dugtrio,Paras   
           267.0                                                                                                                                                                                                                                                                                                                         Persian,Psyduck,Rattata,Dugtrio,Paras   
           268.0                                                                                                                                                                                                                                                                

In [112]:
combined_df

PLANID PLANINVCLOSEDATE                     FUNDID  \
1    VW0008000039           active                   Arcanine   
2    VW0008000039       11/01/2018                   Clefairy   
3    VW0008000039           active                      Zubat   
4    VW0008000039           active                   Nidoking   
5    VW0008000039           active                 Jigglypuff   
6    VW0008000039           active  CharizardMega Charizard X   
8    VW0008000039           active                  Growlithe   
9    VW0008000039           active                     Fearow   
10   VW0008000039           active                      Ekans   
11   VW0008000039           active                      Arbok   
12   VW0008000039           active                     Raichu   
13   VW0008000039           active                  Sandslash   
14   VW0008000039           active                  Nidoqueen   
15   VW0008000039           active                     Oddish   
16   VW0008000039           active                   Clefable   
17   VW0008000039           active                  Vileplume   
18   VW0008000039           active                   Carvanha   
19   VW0008000039           active                  Ninetales   
20   VW0008000039           active                   Primeape   
21   VW0008000039           active                     Vulpix   
22   VW0008000039           active                 Wigglytuff   
23   VW0008000039           active                     Golbat   
24   VW0008000039           active                      Gloom   
25   VW0008000039           active                   Raticate   
26   VW0008000039           active                    Spearow   
27   VW0008000039           active                    Pikachu   
28   VW0008000039           active                  Sandshrew   
29   VW0008000039           active                   Nidorina   
30   VW0008000039           active                   Nidorino   
31   VW0009000188           active                    Poliwag   
32   VW0009000188           active                    Geodude   
33   VW0009000188           active                      Zubat   
34   VW0009000188       07/26/2019                  Poliwhirl   
35   VW0009000188           active                      Golem   
36   VW0009000188           active                   Rapidash   
37   VW0009000188           active                   Rapidash   
38   VW0009000188           active                    Slowbro   
39   VW0009000188           active                    Slowbro   
40   VW0009000188           active                  Magnemite   
41   VW0009000188           active                  Magnemite   
42   VW0009000188           active                 Charmander   
43   VW0009000188           active                       Abra   
44   VW0009000188           active                   Slowpoke   
45   VW0009000188           active                   Slowpoke   
46   VW0009000188           active                  Blastoise   
47   VW0009000188           active                     Machop   
48   VW0009000188           active                    Kadabra   
49   VW0009000188           active                   Squirtle   
50   VW0009000188           active                     Ponyta   
51   VW0009000188           active                     Ponyta   
52   VW0009000188           active                 Farfetch'd   
53   VW0009000188           active                 Farfetch'd   
54   VW0009000188           active                   Venusaur   
55   VW0009000188           active                   Magneton   
56   VW0009000188           active                   Magneton   
57   VW0009000188           active    BlastoiseMega Blastoise   
58   VW0009000188           active        SlowbroMega Slowbro   
59   VW0009000188           active        SlowbroMega Slowbro   
60   VW0009000188           active      VenusaurMega Venusaur   
62   VW0009000188           active                  Poliwrath   
63   VW0009000188           active            

In [113]:
combined_df.fillna('missing', inplace=True)

In [114]:
for index, row in combined_df.iterrows():
    if (row['PLANINVCLOSEDATE'] != 'active') &(row['PLANINVCLOSEDATE']!='missing'):
        #if we have a model_id
        if (row['model_id']!='missing'):
            output_final.at[(row['program_id'],row['model_id']), 'fund_closed'].append(row['FUNDID'])
        #else broadcast across all program_ids
        else:
            idx_2 = output_final.loc[row['partner_program_id']].index
            for i in idx_2:
                output_final.at[(row['partner_program_id'], i), 'fund_closed'].append(row['FUNDID'])


        

In [115]:
output_final

funds_missing_at_partner  \
program_id model_id                                                                                                                                                                                                                                                                                                                                                              
1.0        259.0                                                                                                                                                                                                                                                                                                                         Paras,Phanpy,Venonat,Donphan,Porygon2   
           260.0                                                                                                                                                                                                                                                                                                                  Psyduck,Rattata,Paras,Phanpy,Venonat,Donphan   
           261.0                                                                                                                                                                                                                                                                                                         Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat,Porygon2   
           262.0                                                                                                                                                                                                                                                                                                          Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat   
           263.0                                                                                                                                                                                                                                                                                                                  Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           264.0                                                                                                                                                                                                                                                                                                                  Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           265.0                                                                                                                                                                                                                                                                                                                  Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           266.0                                                                                                                                                                                                                                                                                                                         Persian,Psyduck,Rattata,Dugtrio,Paras   
           267.0                                                                                                                                                                                                                                                                                                                         Persian,Psyduck,Rattata,Dugtrio,Paras   
           268.0                                                                                                                                                                                                                                                                

### Remove fund_closed from funds_missing_at_vw

In [116]:
def fund_closed(funds_closed, funds_missing):
    #cast funds_missing into list format
    try:
        funds_missing = funds_missing.split(',')
    except:
        funds_missing = [funds_missing]
        
    for fund in funds_closed:
        if fund in funds_missing:
            funds_missing.remove(fund)
    try:
        return ','.join(funds_missing)
    except:
        return str(funds_missing)


In [117]:
output_final.funds_missing_at_vw = output_final.apply(lambda x: fund_closed(x.fund_closed,
                                                                            x.funds_missing_at_vw),axis=1)


In [118]:
output_final

funds_missing_at_partner  \
program_id model_id                                                                                                                                                                                                                                                                                                                                                              
1.0        259.0                                                                                                                                                                                                                                                                                                                         Paras,Phanpy,Venonat,Donphan,Porygon2   
           260.0                                                                                                                                                                                                                                                                                                                  Psyduck,Rattata,Paras,Phanpy,Venonat,Donphan   
           261.0                                                                                                                                                                                                                                                                                                         Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat,Porygon2   
           262.0                                                                                                                                                                                                                                                                                                          Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat   
           263.0                                                                                                                                                                                                                                                                                                                  Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           264.0                                                                                                                                                                                                                                                                                                                  Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           265.0                                                                                                                                                                                                                                                                                                                  Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           266.0                                                                                                                                                                                                                                                                                                                         Persian,Psyduck,Rattata,Dugtrio,Paras   
           267.0                                                                                                                                                                                                                                                                                                                         Persian,Psyduck,Rattata,Dugtrio,Paras   
           268.0                                                                                                                                                                                                                                                                

### Clean output_df to look like example

In [119]:
output_final.fillna('missing', inplace=True)

In [120]:
def cleaner(x):
    if (x=='missing')| (x=='nan')|(x=='[nan]')|(x==''):
        return 'None'
    elif (type(x)==set)|(type(x)==list):
        return ','.join(x)
    else:
        return x

In [121]:
output_final.funds_missing_at_vw = output_final.funds_missing_at_vw.apply(cleaner)
output_final.funds_missing_at_partner = output_final.funds_missing_at_partner.apply(cleaner)
output_final.fund_closed = output_final.fund_closed.apply(cleaner)

In [122]:
output_final

funds_missing_at_partner  \
program_id model_id                                                                                                                                                                                                                                                                                                                            
1.0        259.0                                                                                                                                                                                                                                                                                       Paras,Phanpy,Venonat,Donphan,Porygon2   
           260.0                                                                                                                                                                                                                                                                                Psyduck,Rattata,Paras,Phanpy,Venonat,Donphan   
           261.0                                                                                                                                                                                                                                                                       Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat,Porygon2   
           262.0                                                                                                                                                                                                                                                                        Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy,Venonat   
           263.0                                                                                                                                                                                                                                                                                Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           264.0                                                                                                                                                                                                                                                                                Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           265.0                                                                                                                                                                                                                                                                                Persian,Psyduck,Rattata,Dugtrio,Paras,Phanpy   
           266.0                                                                                                                                                                                                                                                                                       Persian,Psyduck,Rattata,Dugtrio,Paras   
           267.0                                                                                                                                                                                                                                                                                       Persian,Psyduck,Rattata,Dugtrio,Paras   
           268.0                                                                                                                                                                                                                                                                                             Persian,Psyduck,Rattata,Dugtrio   
           269.0                                                                                                                                                                                                                                                                    

In [123]:
output_final.reset_index().to_csv('output_df.csv', index=False)